In [1]:
import random
import keras

import numpy as np
import pandas as pd
import tensorflow as tf

import keras.backend as K

from keras.models import Model
from keras.layers import Dense, Input, Dropout, Lambda
from keras.optimizers import Adam
from keras.callbacks import Callback
from scipy.stats import spearmanr, rankdata

from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import KFold
from sklearn.linear_model import MultiTaskElasticNet
from sklearn.linear_model import Ridge
import glob
from sklearn.model_selection import train_test_split

pd.set_option('max_columns', None)
import matplotlib.pyplot as plt
import seaborn as sns
plt.style.use('seaborn')
%matplotlib inline

random.seed(42)

Using TensorFlow backend.
C:\Users\user\AppData\Local\Programs\Python\Python37\lib\site-packages\requests\__init__.py:91: RequestsDependencyWarning: urllib3 (1.26.8) or chardet (3.0.4) doesn't match a supported version!
  RequestsDependencyWarning)


# Loading the data

In [2]:
stv=pd.read_csv('sales_train_validation.csv')
cal=pd.read_csv('calendar.csv')

In [3]:
stv_df = stv.drop(['item_id', 'dept_id', 'cat_id', 'store_id', 'state_id'], axis=1).set_index('id').T
stv_df['d'] = stv_df.index

In [4]:
df = pd.merge(cal, stv_df, left_on='d', right_on='d', how='left')

In [5]:
def event_detector(x):
    if x == None:
        return 0
    else:
        return 1

In [6]:
#drop the date we won't use
drp = ['wm_yr_wk', 'weekday', 'year', 'd', 'event_type_1', 'event_type_2']

#we will use these columns
cols_x = ['wday', 'month', 'event_name_1', 'event_name_2','snap_CA', 'snap_TX', 'snap_WI']


# process events to binary
df = df.drop(drp, axis=1)
df['event_name_1'] = df['event_name_1'].apply(lambda x: event_detector(x))
df['event_name_2'] = df['event_name_2'].apply(lambda x: event_detector(x))

In [7]:
# separate validation data and evaluation data
ddf = df[(pd.to_datetime(df['date']) < '2016-04-25')&(pd.to_datetime(df['date']) >= '2015-06-19')].drop('date', axis=1)
valid_df = df[(pd.to_datetime(df['date']) >= '2016-04-25')&(pd.to_datetime(df['date']) < '2016-05-23')].drop('date', axis=1)
eval_df = df[pd.to_datetime(df['date']) >= '2016-05-23'].drop('date', axis=1)

In [8]:
ddf.head(1)

wday  month  event_name_1  event_name_2  snap_CA  snap_TX  snap_WI  \
1602     7      6             1             1        0        0        0   

      HOBBIES_1_001_CA_1_validation  HOBBIES_1_002_CA_1_validation  \
1602                            3.0                            0.0   

      HOBBIES_1_003_CA_1_validation  HOBBIES_1_004_CA_1_validation  \
1602                            1.0                            2.0   

      HOBBIES_1_005_CA_1_validation  HOBBIES_1_006_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_007_CA_1_validation  HOBBIES_1_008_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_009_CA_1_validation  HOBBIES_1_010_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_011_CA_1_validation  HOBBIES_1_012_CA_1_validation  \
1602                            1.0                            0.0   

      HOBBIES_1_013_CA_1_validation  HOBBIES_1_014_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_015_CA_1_validation  HOBBIES_1_016_CA_1_validation  \
1602                            5.0                            3.0   

      HOBBIES_1_017_CA_1_validation  HOBBIES_1_018_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_019_CA_1_validation  HOBBIES_1_020_CA_1_validation  \
1602                           14.0                            0.0   

      HOBBIES_1_021_CA_1_validation  HOBBIES_1_022_CA_1_validation  \
1602                            0.0                            1.0   

      HOBBIES_1_023_CA_1_validation  HOBBIES_1_024_CA_1_validation  \
1602                            2.0                            0.0   

      HOBBIES_1_025_CA_1_validation  HOBBIES_1_026_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_027_CA_1_validation  HOBBIES_1_028_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_029_CA_1_validation  HOBBIES_1_030_CA_1_validation  \
1602                            1.0                            0.0   

      HOBBIES_1_031_CA_1_validation  HOBBIES_1_032_CA_1_validation  \
1602                            0.0                           14.0   

      HOBBIES_1_033_CA_1_validation  HOBBIES_1_034_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_035_CA_1_validation  HOBBIES_1_036_CA_1_validation  \
1602                            1.0                            0.0   

      HOBBIES_1_037_CA_1_validation  HOBBIES_1_038_CA_1_validation  \
1602                            1.0                            1.0   

      HOBBIES_1_039_CA_1_validation  HOBBIES_1_040_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_041_CA_1_validation  HOBBIES_1_042_CA_1_validation  \
1602                            0.0                            1.0   

      HOBBIES_1_043_CA_1_validation  HOBBIES_1_044_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_045_CA_1_validation  HOBBIES_1_046_CA_1_validation  \
1602                            1.0                            0.0   

      HOBBIES_1_047_CA_1_validation  HOBBIES_1_048_CA_1_validation  \
1602                            0.0                           16.0   

      HOBBIES_1_049_CA_1_validation  HOBBIES_1_050_CA_1_validation  \
1602                            2.0                            1.0   

      HOBBIES_1_051_CA_1_validation  HOBBIES_1_052_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_053_CA_1_validation  HOBBIES_1_054_CA_1_validation  \
1602                            0.0                            0.0   

      HOBBIES_1_055_CA_1_validation  HOBBIES_1

In [9]:
X_ddf = ddf[cols_x]
y_ddf = ddf.drop(cols_x, axis=1)

X_train, X_test, y_train, y_test = train_test_split(
         X_ddf, y_ddf, test_size=0.33, random_state=42)

In [15]:
y_test.head(1)

In [16]:
y_train.shape[1]

In [18]:
model.metrics_names

In [17]:
score

In [9]:
from keras.models import Sequential
from keras.layers import Dense, Activation
from keras.callbacks import TensorBoard
import keras.backend as K
EarlyStopping = tf.keras.callbacks.EarlyStopping()


def rmse(y_true, y_pred):
    return K.sqrt(K.mean(K.square(y_pred -y_true)))

epochs=250
batch_size = 96
verbose = 1
validation_split = 0.2
input_dim = X_train.shape[1]
n_out = y_train.shape[1]

model = Sequential([
                Dense(512, input_shape=(input_dim,)),
                Activation('relu'),
                Dropout(0.2),
                Dense(512),
                Activation('relu'),
                Dropout(0.2),
                Dense(n_out),
                Activation('relu'),
                    ])

model.compile(loss='mse',
                 optimizer='adam',
                 metrics=['mse', rmse])
hist = model.fit(X_train, y_train,
                         batch_size = batch_size, epochs = epochs,
                         callbacks = [EarlyStopping],
                         verbose=verbose, validation_split=validation_split)

score = model.evaluate(X_test, y_test, verbose=verbose)
print("\nTest score:", score[0])

In [10]:
plt.clf()
plt.figsize=(15, 10)
loss = hist.history['loss']
val_loss = hist.history['val_loss']
epochs = range(1, len(loss) +1)

plt.plot(epochs, loss, 'bo', label = 'Training loss')
plt.plot(epochs, val_loss, 'b', label = 'Validation loss')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.legend()

plt.show()

In [11]:
# import shap
# df_train_normed = X_train
# df_train_normed_summary = shap.kmeans(df_train_normed.values, 25)
# # Instantiate an explainer with the model predictions and training data summary
# explainer = shap.KernelExplainer(model.predict, df_train_normed_summary)
# # Extract Shapley values from the explainer
# shap_values = explainer.shap_values(df_train_normed.values)

# make prediction

In [ ]:
X_valid = valid_df[cols_x]
X_eval = eval_df[cols_x]

# predict validation and evaluation respectively
pred_valid = pd.DataFrame(model.predict(X_valid), columns = ss[0:int(len(ss)/2)].set_index('id').T.columns)
pred_eval = pd.DataFrame(model.predict(X_eval), columns = ss[int(len(ss)/2):].set_index('id').T.columns)
ss_valid =  pred_valid.T
ss_eval = pred_eval.T

# concatenate val and eval
submission_df = pd.concat([ss_valid, ss_eval]).reset_index()
submission_df.columns = ss.columns

submission_df.head()

In [ ]:
#check some of prediction
d_cols = [c for c in submission_df.columns if 'F' in c]
pred_example = submission_df.sample(10, random_state=2020).set_index('id')[d_cols].T

fig, axs = plt.subplots(5, 2, figsize=(15, 10))
axs = axs.flatten()
ax_idx = 0
for item in pred_example.columns:
    pred_example[item].plot(title=item,
                              ax=axs[ax_idx])
    ax_idx += 1
plt.tight_layout()
plt.show()

In [ ]:
submission_df.to_csv('submission.csv', index=False)